# View SSNet Images

This notebook is here to let one inspect ssnet images.

In [1]:
# python
import os,sys
import shutil
import time
import traceback

# numpy
import numpy as np

# ROOT/LArCV
import ROOT
from larcv import larcv

# matplotlib
%matplotlib notebook
%matplotlib inline
import matplotlib.pyplot as plt

Welcome to JupyROOT 6.08/06


In [2]:
# Set data file here
input_ssnet_out="~/working/larbys/dllee_unified/ssnetout_larcv_0000.root"

In [3]:
# Setup LArCV IO


io = larcv.IOManager()
io.add_in_file( input_ssnet_out )
io.initialize()

True

    [NORMAL]  <IOManager::prepare_input> Opening a file in READ mode: ~/working/larbys/dllee_unified/ssnetout_larcv_0000.root
    [NORMAL]  <IOManager::initialize> Prepared input with 189 entries...


In [4]:
# Set Entry
use_rse = False # set to True to use (run,subrun,event). Else will use entry number
entry = 10
run = None
subrun = None
event = None

In [5]:
# Retrieve entry
readok = False
if not use_rse:
    readok = io.read_entry( entry )
print readok
if readok:
    evbase = io.event_id()
    print "Read Run,subrun,event=(%d,%d,%d)"%(evbase.run(), evbase.subrun(), evbase.event())

True
Read Run,subrun,event=(18446744073709551615,18446744073709551615,18446744073709551615)


In [30]:
# Get image containers
ev_modimg  = io.get_data(larcv.kProductImage2D,"modimg")
ev_uburn = {}
ev_uburn[0] = io.get_data(larcv.kProductImage2D,"uburn_plane0")
ev_uburn[1] = io.get_data(larcv.kProductImage2D,"uburn_plane1")
ev_uburn[2] = io.get_data(larcv.kProductImage2D,"uburn_plane2")

# get images
meta = ev_modimg.Image2DArray().at(0).meta()

tpcimgs = np.zeros( (3,meta.cols(),meta.rows()) )
showerscore = np.zeros( (3,meta.cols(),meta.rows()) )
trackscore  = np.zeros( (3,meta.cols(),meta.rows()) )
combined = {}

# we make an image where empty pixels are white
# pixels with track/shower score are in red and blue scales
for plane in range(0,3):
    tpcimgs[plane,:,:]     = larcv.as_ndarray( ev_modimg.Image2DArray().at(plane) )
    combined[plane] = np.zeros( (meta.cols(),meta.rows(),3) )
    
    combined[plane][:,:,0] = tpcimgs[plane,:,:]
    combined[plane][:,:,1] = tpcimgs[plane,:,:]
    combined[plane][:,:,2] = tpcimgs[plane,:,:]
    
    # threshold
    combined[plane][combined[plane]<10.0] = 10.0
    combined[plane] -= 10.0
    
    # cap
    combined[plane][combined[plane]>100.0] = 100.0
    
    # rescale
    combined[plane] /= 100.0
    
    # set from white to black
    combined[plane] = 1.0-combined[plane]
    
    roimeta = ev_uburn[plane].Image2DArray().at(0).meta()
    mincol = meta.col( roimeta.min_x() )
    minrow = meta.row( roimeta.max_y() )
    showerscore[plane,mincol:mincol+roimeta.cols(),minrow:minrow+roimeta.rows()] = larcv.as_ndarray( ev_uburn[plane].Image2DArray().at(0) )
    trackscore[plane, mincol:mincol+roimeta.cols(),minrow:minrow+roimeta.rows()] = larcv.as_ndarray( ev_uburn[plane].Image2DArray().at(1) )
    
    # zero region with tags
    combined[plane][mincol:mincol+roimeta.cols(),minrow:minrow+roimeta.rows(),:] = 0
    
    
    combslice = combined[plane][mincol:mincol+roimeta.cols(),minrow:minrow+roimeta.rows(),:]
    showerslice = showerscore[plane,mincol:mincol+roimeta.cols(),minrow:minrow+roimeta.rows()]
    trackslice  = trackscore[plane,mincol:mincol+roimeta.cols(),minrow:minrow+roimeta.rows()]
    
    # red channel to shower
    combslice[:,:,0] = showerslice
    
    # blue channel to track
    combslice[:,:,2] = trackslice
    
    st = showerslice+trackslice
    combslice[:,:,1][st==0] = 1.0
    combslice[:,:,0][st==0] = 1.0
    combslice[:,:,2][st==0] = 1.0
    
    # transpose combined
    combined[plane] = np.transpose( combined[plane], (1,0,2) )

tpcimgs     = np.transpose( tpcimgs, (0,2,1) )
showerscore = np.transpose( showerscore, (0,2,1) )
trackscore  = np.transpose( trackscore, (0,2,1) )


/usr/local/lib/python2.7/dist-packages/ipykernel_launcher.py:17: DeprecationWarning: PyArray_FromDimsAndDataAndDescr: use PyArray_NewFromDescr.
/usr/local/lib/python2.7/dist-packages/ipykernel_launcher.py:40: DeprecationWarning: PyArray_FromDimsAndDataAndDescr: use PyArray_NewFromDescr.
/usr/local/lib/python2.7/dist-packages/ipykernel_launcher.py:41: DeprecationWarning: PyArray_FromDimsAndDataAndDescr: use PyArray_NewFromDescr.


In [33]:
# make pictures
# this takes awhile, due to large image sizes

for p in range(0,3):
    fig = plt.figure(figsize=(3456/12,1008/12))
    #fig = plt.figure()
    plt.imshow(combined[p])